In [2]:
import os
import pandas as pd
from skimage import io, transform
from skimage.measure import label, regionprops
import numpy as np
import matplotlib.pyplot as plt

from PIL import Image
from skimage.transform import resize

from scipy import ndimage
import glob
import nibabel as nib
from nilearn import image

pd.options.display.max_colwidth = 100
import shutil
import copy
import radiomics


In [3]:
test_set = pd.read_csv("/home/asrar/Documents/preprocessed/training_with_val_split.csv")

In [4]:
ID = test_set["paths"].apply(lambda l: l.split('/')[6])
test_set.insert(5,'ID' ,ID )

In [6]:
test_set["ID"].astype('int64', copy=False)
p = int(test_set["ID"][0])

In [7]:
def Skewness_Core_T1w (image,mask):
    settings = {}
    settings['binWidth'] = 5
    settings['resampledPixelSpacing'] = None
    settings['normalize'] = False
    image =sitk.ReadImage(image)
    mask =sitk.ReadImage(mask)
    firstOrderFeatures1 = firstorder.RadiomicsFirstOrder(image,mask, label=2&3,**settings)
    firstOrderFeatures1.enableAllFeatures()  
    firstOrderFeatures1.calculateFeatures()
    Skewness = firstOrderFeatures1.featureValues.get("Skewness")
    x = Skewness.astype(np.float)
    print(Skewness)
    return x

In [8]:
def Energy_Oedema_T1W (image,mask):
    settings = {}
    settings['binWidth'] = 5
    settings['resampledPixelSpacing'] = None
    settings['normalize'] = False
    image =sitk.ReadImage(image)
    mask =sitk.ReadImage(mask)
    firstOrderFeatures = firstorder.RadiomicsFirstOrder(image,mask, label=1,**settings)
    firstOrderFeatures.enableAllFeatures()  
    firstOrderFeatures.calculateFeatures()
    Energy = firstOrderFeatures.featureValues.get("Energy")
    return Energy

In [9]:
def GLCM_Contrast_Necrosis_FLAIR (image,mask):
    settings = {}
    settings['binWidth'] = 5
    settings['resampledPixelSpacing'] = None
    settings['normalize'] = False
    image =sitk.ReadImage(image)
    mask =sitk.ReadImage(mask)
    glcmFeatures = glcm.RadiomicsGLCM(image,mask, label=3,**settings)
    glcmFeatures.enableAllFeatures() 
    glcmFeatures.calculateFeatures()
    Contrast = glcmFeatures.featureValues.get("Contrast")
    return Contrast


In [10]:
def GLSZM_Grey_Level_Variance_Enhanced_T1c (image,mask):
    settings = {}
    settings['binWidth'] = 5
    settings['resampledPixelSpacing'] = None
    settings['normalize'] = False
    image =sitk.ReadImage(image)
    mask =sitk.ReadImage(mask)
    glszmFeatures1 = glszm.RadiomicsGLSZM(image,mask, label=3,**settings)
    glszmFeatures1.enableAllFeatures()  
    glszmFeatures1.calculateFeatures()
    GrayLevelVariance = glszmFeatures1.featureValues.get("GrayLevelVariance")
    return GrayLevelVariance

In [11]:
def GLSZM_LowGrayLevelZoneEmphasis_Oedema_T2w (image,mask):
    settings = {}
    settings['binWidth'] = 5
    settings['resampledPixelSpacing'] = None
    settings['normalize'] = False
    image =sitk.ReadImage(image)
    mask =sitk.ReadImage(mask)
    glszmFeatures = glszm.RadiomicsGLSZM(image,mask, label=1,**settings)
    glszmFeatures.enableAllFeatures() 
    glszmFeatures.calculateFeatures()
    LowGrayLevelZoneEmphasis = glszmFeatures.featureValues.get("LowGrayLevelZoneEmphasis")
    return LowGrayLevelZoneEmphasis

In [12]:
def original_ngtdm_Busyness_Core_T2w (image,mask):
    settings = {}
    settings['binWidth'] = 5
    settings['resampledPixelSpacing'] = None
    settings['normalize'] = False
    image =sitk.ReadImage(image)
    mask =sitk.ReadImage(mask)
    ngtdmFeatures = ngtdm.RadiomicsNGTDM(image,mask, label=2&3,**settings)
    ngtdmFeatures.enableAllFeatures() 
    ngtdmFeatures.calculateFeatures()
    Busyness = ngtdmFeatures.featureValues.get("Busyness")
    return Busyness

In [14]:
import SimpleITK as sitk
import os
import pandas as pd
from tqdm import tqdm
import numpy as np
from radiomics import firstorder, getTestCase, glcm, glrlm, glszm, imageoperations, shape,ngtdm
T1c_filename = "T1wCE/T1CE_to_SRI.nii.gz"
T1_filename = "T1w/T1_to_SRI.nii.gz"
T2_filename = "T2w/T2_to_SRI.nii.gz"
fl_filename = "FLAIR/FL_to_SRI.nii.gz"
mask_suffix = "/home/asrar/Documents/segmented_real_ids/train/BRATS_"

rootdir_onlysurv = "/home/asrar/Documents/preprocessed/train/"

osinfo = test_set

subjlist = list(osinfo["ID"])


overallfeatdf = pd.DataFrame(data=[],
                             columns=['Skewness_Core_T1w',
                                                   'Energy_Oedema_T1W',
                                                   'GLCM_Contrast_Necrosis_FLAIR',
                                                   'GLSZM_Grey Level Variance_Enhanced_T1c',
                                                   'GLSZM_Low Grey Level Zone Emphasis_Oedema_T2w',
                                                   'original_ngtdm_Busyness_Core_T2w'])

overallfeatdf.index.name = "ID"

Skewness =[]
Energy =[]
Contrast=[]
Variance=[]
Emphasis=[]
Busyness =[]

for subj in tqdm(subjlist):
   
    currsubjdir1 = os.path.join(rootdir_onlysurv+subj+'/T1wCE/T1CE_to_SRI.nii.gz')
    currsubjdir2 = os.path.join(rootdir_onlysurv+subj+'/T1w/T1_to_SRI.nii.gz')
    currsubjdir3 = os.path.join(rootdir_onlysurv+subj+'/T2w/T2_to_SRI.nii.gz')
    currsubjdir4 = os.path.join(rootdir_onlysurv+subj+'/FLAIR/FL_to_SRI.nii.gz')
    p = int(subj)
    p2= str("{:04d}".format(p))
    maskpath = os.path.join(mask_suffix+p2+'.nii.gz')
    print(maskpath)
    print(currsubjdir2)
    try:
        featureVector = Skewness_Core_T1w (currsubjdir2,maskpath)
        featureVector2 = Energy_Oedema_T1W (currsubjdir2,maskpath)
        featureVector3 = GLCM_Contrast_Necrosis_FLAIR(currsubjdir4,maskpath)
        featureVector4 = GLSZM_Grey_Level_Variance_Enhanced_T1c(currsubjdir1,maskpath)
        featureVector5 = GLSZM_LowGrayLevelZoneEmphasis_Oedema_T2w(currsubjdir3,maskpath)
        featureVector6 = original_ngtdm_Busyness_Core_T2w(currsubjdir3,maskpath)
    except:
        pass
        
    Skewness.append(featureVector)
    Energy.append(featureVector2)
    Contrast.append(featureVector3)
    Variance.append(featureVector4)
    Emphasis.append(featureVector5)
    Busyness.append(featureVector6)
    
    currfeaturedf = pd.DataFrame(data=[[Skewness,Energy,Contrast,Variance,Emphasis,Busyness]] ,index=[subj], columns=['Skewness_Core_T1w',
                                                   'Energy_Oedema_T1W',
                                                   'GLCM_Contrast_Necrosis_FLAIR',
                                                   'GLSZM_Grey Level Variance_Enhanced_T1c',
                                                   'GLSZM_Low Grey Level Zone Emphasis_Oedema_T2w',
                                                   'original_ngtdm_Busyness_Core_T2w'])
    print(currfeaturedf)

    overallfeatdf = overallfeatdf.append(currfeaturedf, sort =False)
overallfeatdf.to_csv('/home/asrar/Documents/Train_RAD.csv')

  0%|          | 0/1664 [00:00<?, ?it/s]

/home/asrar/Documents/segmented_real_ids/train/BRATS_0239.nii.gz
/home/asrar/Documents/preprocessed/train/00239/T1w/T1_to_SRI.nii.gz


calculateFeatures() is deprecated, use execute() instead.
calculateFeatures() is deprecated, use execute() instead.


0.7702210295016941


calculateFeatures() is deprecated, use execute() instead.
GLCM is symmetrical, therefore Sum Average = 2 * Joint Average, only 1 needs to be calculated
calculateFeatures() is deprecated, use execute() instead.
calculateFeatures() is deprecated, use execute() instead.
calculateFeatures() is deprecated, use execute() instead.
  0%|          | 1/1664 [00:01<50:18,  1.81s/it]calculateFeatures() is deprecated, use execute() instead.


...

                                                                                         Skewness_Core_T1w  \
01010  [0.7702210295016941, 0.7702210295016941, 0.7702210295016941, 0.7702210295016941, 0.3074381087812...   

                                                                                         Energy_Oedema_T1W  \
01010  [4018358614.719592, 4018358614.719592, 4018358614.719592, 4018358614.719592, 2605376540.5535407,...   

                                                                              GLCM_Contrast_Necrosis_FLAIR  \
01010  [125.87479673466352, 125.87479673466352, 125.87479673466352, 125.87479673466352, 132.77853522521...   

                                                                    GLSZM_Grey Level Variance_Enhanced_T1c  \
01010  [671.2997349251181, 671.2997349251181, 671.2997349251181, 671.2997349251181, 998.8855608274262, ...   

                                                             GLSZM_Low Grey Level Zone Emphasis_Oedema_T2w  \
01010 

calculateFeatures() is deprecated, use execute() instead.
calculateFeatures() is deprecated, use execute() instead.
GLCM is symmetrical, therefore Sum Average = 2 * Joint Average, only 1 needs to be calculated
calculateFeatures() is deprecated, use execute() instead.
calculateFeatures() is deprecated, use execute() instead.
calculateFeatures() is deprecated, use execute() instead.
100%|█████████▉| 1663/1664 [2:43:50<00:02,  2.67s/it]calculateFeatures() is deprecated, use execute() instead.


                                                                                         Skewness_Core_T1w  \
01010  [0.7702210295016941, 0.7702210295016941, 0.7702210295016941, 0.7702210295016941, 0.3074381087812...   

                                                                                         Energy_Oedema_T1W  \
01010  [4018358614.719592, 4018358614.719592, 4018358614.719592, 4018358614.719592, 2605376540.5535407,...   

                                                                              GLCM_Contrast_Necrosis_FLAIR  \
01010  [125.87479673466352, 125.87479673466352, 125.87479673466352, 125.87479673466352, 132.77853522521...   

                                                                    GLSZM_Grey Level Variance_Enhanced_T1c  \
01010  [671.2997349251181, 671.2997349251181, 671.2997349251181, 671.2997349251181, 998.8855608274262, ...   

                                                             GLSZM_Low Grey Level Zone Emphasis_Oedema_T2w  \
01010 

calculateFeatures() is deprecated, use execute() instead.
calculateFeatures() is deprecated, use execute() instead.
GLCM is symmetrical, therefore Sum Average = 2 * Joint Average, only 1 needs to be calculated
calculateFeatures() is deprecated, use execute() instead.
calculateFeatures() is deprecated, use execute() instead.
calculateFeatures() is deprecated, use execute() instead.
100%|██████████| 1664/1664 [2:43:52<00:00,  5.91s/it]


                                                                                         Skewness_Core_T1w  \
01010  [0.7702210295016941, 0.7702210295016941, 0.7702210295016941, 0.7702210295016941, 0.3074381087812...   

                                                                                         Energy_Oedema_T1W  \
01010  [4018358614.719592, 4018358614.719592, 4018358614.719592, 4018358614.719592, 2605376540.5535407,...   

                                                                              GLCM_Contrast_Necrosis_FLAIR  \
01010  [125.87479673466352, 125.87479673466352, 125.87479673466352, 125.87479673466352, 132.77853522521...   

                                                                    GLSZM_Grey Level Variance_Enhanced_T1c  \
01010  [671.2997349251181, 671.2997349251181, 671.2997349251181, 671.2997349251181, 998.8855608274262, ...   

                                                             GLSZM_Low Grey Level Zone Emphasis_Oedema_T2w  \
01010 

In [20]:
for i in Busyness:
    print (float(i))

0.0185036139971758
0.0185036139971758
0.0185036139971758
0.0185036139971758
0.00426851836960624
0.00426851836960624
0.00426851836960624
0.00426851836960624
0.031626238281193327
0.031626238281193327
0.031626238281193327
0.031626238281193327
0.13456354274144622
0.13456354274144622
0.13456354274144622
0.13456354274144622
0.01741665893722973
0.01741665893722973
0.01741665893722973
0.01741665893722973
0.01741665893722973
0.01741665893722973
0.01741665893722973
0.01741665893722973
0.006340635134366977
0.006340635134366977
0.006340635134366977
0.006340635134366977
0.0250996478518418
0.0250996478518418
0.0250996478518418
0.0250996478518418
0.030389488566905216
0.030389488566905216
0.030389488566905216
0.030389488566905216
0.00796259549309164
0.00796259549309164
0.00796259549309164
0.00796259549309164
0.02189828925918152
0.02189828925918152
0.02189828925918152
0.02189828925918152
0.02189828925918152
0.02189828925918152
0.02189828925918152
0.02189828925918152
0.02189828925918152
0.02189828925918

In [21]:
for i in Skewness:
    print (float(i))

0.7702210295016941
0.7702210295016941
0.7702210295016941
0.7702210295016941
0.3074381087812178
0.3074381087812178
0.3074381087812178
0.3074381087812178
0.9377580668673249
0.9377580668673249
0.9377580668673249
0.9377580668673249
-1.3443401985311614
-1.3443401985311614
-1.3443401985311614
-1.3443401985311614
-0.38265998856205685
-0.38265998856205685
-0.38265998856205685
-0.38265998856205685
1.7784228783089806
1.7784228783089806
1.7784228783089806
1.7784228783089806
-1.5479405498983232
-1.5479405498983232
-1.5479405498983232
-1.5479405498983232
0.7761629384275076
0.7761629384275076
0.7761629384275076
0.7761629384275076
-1.2500053955447923
-1.2500053955447923
-1.2500053955447923
-1.2500053955447923
1.4498745197736436
1.4498745197736436
1.4498745197736436
1.4498745197736436
0.6733820390106359
0.6733820390106359
0.6733820390106359
0.6733820390106359
0.712586521985233
0.712586521985233
0.712586521985233
0.712586521985233
-1.9695337114471523
-1.9695337114471523
-1.9695337114471523
-1.969533711